# Data drift dashboard in jupyter notebook

In [1]:
import pandas as pd
import numpy as np

from datetime import datetime
from sklearn import datasets, ensemble

from evidently.dashboard import Dashboard
from evidently.tabs import DataDriftTab, NumTargetDriftTab, RegressionPerformanceTab

## Bicycle Demand Data

In [2]:
raw_data = pd.read_csv('../../train.csv', header=0, sep=',', parse_dates=['datetime'], index_col='datetime')

In [3]:
raw_data.head()

season  holiday  workingday  weather  temp   atemp  \
datetime                                                                  
2011-01-01 00:00:00       1        0           0        1  9.84  14.395   
2011-01-01 01:00:00       1        0           0        1  9.02  13.635   
2011-01-01 02:00:00       1        0           0        1  9.02  13.635   
2011-01-01 03:00:00       1        0           0        1  9.84  14.395   
2011-01-01 04:00:00       1        0           0        1  9.84  14.395   

                     humidity  windspeed  casual  registered  count  
datetime                                                             
2011-01-01 00:00:00        81        0.0       3          13     16  
2011-01-01 01:00:00        80        0.0       8          32     40  
2011-01-01 02:00:00        80        0.0       5          27     32  
2011-01-01 03:00:00        75        0.0       3          10     13  
2011-01-01 04:00:00        75        0.0       0           1      1

## Regression Model

### Feature engineering

In [4]:
raw_data['month'] = raw_data.index.map(lambda x : x.month)
raw_data['hour'] = raw_data.index.map(lambda x : x.hour)
raw_data['weekday'] = raw_data.index.map(lambda x : x.weekday() + 1)

In [5]:
raw_data.head()

season  holiday  workingday  weather  temp   atemp  \
datetime                                                                  
2011-01-01 00:00:00       1        0           0        1  9.84  14.395   
2011-01-01 01:00:00       1        0           0        1  9.02  13.635   
2011-01-01 02:00:00       1        0           0        1  9.02  13.635   
2011-01-01 03:00:00       1        0           0        1  9.84  14.395   
2011-01-01 04:00:00       1        0           0        1  9.84  14.395   

                     humidity  windspeed  casual  registered  count  month  \
datetime                                                                     
2011-01-01 00:00:00        81        0.0       3          13     16      1   
2011-01-01 01:00:00        80        0.0       8          32     40      1   
2011-01-01 02:00:00        80        0.0       5          27     32      1   
2011-01-01 03:00:00        75        0.0       3          10     13      1   
2011-01-01 04:00:00        75        0.0       0           1      1      1   

                     hour  weekday  
datetime                            
2011-01-01 00:00:00     0        6  
2011-01-01 01:00:00     1        6  
2011-01-01 02:00:00     2        6  
2011-01-01 03:00:00     3        6  
2011-01-01 04:00:00     4        6

### Model training

In [6]:
target = 'count'
prediction = 'prediction'
numerical_features = ['temp', 'atemp', 'humidity', 'windspeed', 'hour', 'weekday']
categorical_features = ['season', 'holiday', 'workingday']

In [7]:
reference = raw_data.loc['2011-01-01 00:00:00':'2011-01-28 23:00:00']
production = raw_data.loc['2011-01-29 00:00:00':'2011-02-28 23:00:00']

In [8]:
reference.head()

season  holiday  workingday  weather  temp   atemp  \
datetime                                                                  
2011-01-01 00:00:00       1        0           0        1  9.84  14.395   
2011-01-01 01:00:00       1        0           0        1  9.02  13.635   
2011-01-01 02:00:00       1        0           0        1  9.02  13.635   
2011-01-01 03:00:00       1        0           0        1  9.84  14.395   
2011-01-01 04:00:00       1        0           0        1  9.84  14.395   

                     humidity  windspeed  casual  registered  count  month  \
datetime                                                                     
2011-01-01 00:00:00        81        0.0       3          13     16      1   
2011-01-01 01:00:00        80        0.0       8          32     40      1   
2011-01-01 02:00:00        80        0.0       5          27     32      1   
2011-01-01 03:00:00        75        0.0       3          10     13      1   
2011-01-01 04:00:00        75        0.0       0           1      1      1   

                     hour  weekday  
datetime                            
2011-01-01 00:00:00     0        6  
2011-01-01 01:00:00     1        6  
2011-01-01 02:00:00     2        6  
2011-01-01 03:00:00     3        6  
2011-01-01 04:00:00     4        6

In [9]:
regressor = ensemble.RandomForestRegressor(random_state = 0, n_estimators = 50)

In [10]:
regressor.fit(reference[numerical_features + categorical_features], reference[target])

RandomForestRegressor(n_estimators=50, random_state=0)

In [11]:
ref_prediction = regressor.predict(reference[numerical_features + categorical_features])
prod_prediction = regressor.predict(production[numerical_features + categorical_features])

In [12]:
reference['prediction'] = ref_prediction
production['prediction'] = prod_prediction

### Model Perfomance 

In [13]:
column_mapping = {}

column_mapping['target'] = target
column_mapping['prediction'] = prediction
column_mapping['numerical_features'] = numerical_features
column_mapping['categorical_features'] = categorical_features

In [14]:
regression_perfomance_dashboard = Dashboard(tabs=[RegressionPerformanceTab])
regression_perfomance_dashboard.calculate(reference, None, column_mapping=column_mapping)

In [15]:
regression_perfomance_dashboard.show()

In [16]:
#regression_perfomance_dashboard.save('regression_performance_at_training.html')

##  Week 1

In [17]:
regression_perfomance_dashboard.calculate(reference, production.loc['2011-01-29 00:00:00':'2011-02-07 23:00:00'], 
                                            column_mapping=column_mapping)

In [18]:
regression_perfomance_dashboard.show()

In [19]:
#regression_perfomance_dashboard.save('regression_performance_after_week1.html')

In [20]:
target_drift_dashboard = Dashboard(tabs=[NumTargetDriftTab])
target_drift_dashboard.calculate(reference, production.loc['2011-01-29 00:00:00':'2011-02-07 23:00:00'], 
                                   column_mapping=column_mapping)

In [21]:
target_drift_dashboard.show()

In [22]:
#target_drift_dashboard.save('target_drift_after_week1.html')

## Week 2

In [23]:
regression_perfomance_dashboard.calculate(reference, production.loc['2011-02-07 00:00:00':'2011-02-14 23:00:00'], 
                                            column_mapping=column_mapping)

In [24]:
regression_perfomance_dashboard.show()

In [25]:
#regression_perfomance_dashboard.save('regression_performance_after_week2.html')

In [26]:
target_drift_dashboard.calculate(reference, production.loc['2011-02-07 00:00:00':'2011-02-14 23:00:00'], 
                                   column_mapping=column_mapping)

In [27]:
target_drift_dashboard.show()

In [28]:
#target_drift_dashboard.save('target_drift_after_week2.html')

## Week 3

In [29]:
regression_perfomance_dashboard.calculate(reference, production.loc['2011-02-15 00:00:00':'2011-02-21 23:00:00'], 
                                            column_mapping=column_mapping)

In [30]:
regression_perfomance_dashboard.show()

In [31]:
#regression_perfomance_dashboard.save('regression_performance_after_week3.html')

In [32]:
target_drift_dashboard.calculate(reference, production.loc['2011-02-15 00:00:00':'2011-02-21 23:00:00'], 
                                   column_mapping=column_mapping)

In [33]:
target_drift_dashboard.show()

In [34]:
#target_drift_dashboard.save('target_drift_after_week3.html')

## Data Drift

In [35]:
column_mapping = {}

column_mapping['numerical_features'] = numerical_features

In [37]:
data_drift_dashboard = Dashboard(tabs=[DataDriftTab])
data_drift_dashboard.calculate(reference, production.loc['2011-01-29 00:00:00':'2011-02-07 23:00:00'], 
                                   column_mapping=column_mapping)

In [38]:
data_drift_dashboard.show()

In [39]:
#data_drift_dashboard.save("data_drift_dashboard_after_week1.html")